# 7. V410 Tau Corner Plot

## 7.1. Notebook setup

In [1]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import emcee
import corner
import warnings
warnings.filterwarnings('ignore')

## 7.2. <a href="https://www.dropbox.com/s/dbpnl57wmuujv6w/V410Tau_corner-plot.zip?dl=1">Download data</a>

Unzip the contents into a folder named <font color='green'>data</font> in the same level as the notebooks folder. The directory structure should end up looking like the following: 
```
thermal-gs
├── data
│   ├── thermal-gs.mplstyle
│   ├── V410Tau_chain.h5
│   ├── V410Tau_lmfit_params.txt
│   ├── ...
├── figures
│   ├── V410Tau_corner.pdf
│   ├── V410Tau_corner.png
│   ├── ...
├── notebooks
│   ├── V410Tau_corner-plot.ipynb
│   ├── ...
.
.
.

## 7.3. Load

In [2]:
sampler = emcee.backends.HDFBackend('../data/V410Tau_chain.h5')
samples = sampler.get_chain(flat=True)
samples /= np.array([1, 1, 1, 1, np.pi/180, 1, 1, 1, 1, np.pi/180])
lmfit_params = np.loadtxt('../data/V410Tau_lmfit_params.txt')
lmfit_params /= np.array([1, 1, 1, 1, np.pi/180, 1, 1, 1, 1, np.pi/180])

plt.style.use('../data/thermal-gs.mplstyle')

## 7.4. Plot

In [3]:
thin = 10000
plt_labels = [r'$L_{\rm pwr}$', '$\delta$', r'$n_{e,{\rm pwr}}$', r'$B_{\rm pwr}$', r'$\phi_{\rm pwr}$', r'$L_{\rm th}$', '$T_e$', r'$n_{e,{\rm th}}$', r'$B_{\rm th}$', r'$\phi_{\rm th}$']
median_values = np.median(samples[::thin, :], axis=0)
cmap = mpl.cm.get_cmap('Purples')
cmap.set_under(color='w')

cornerFig = corner.corner(samples[::thin, :],color='black',top_ticks=True,quiet=True, show_titles=True,use_math_text=True,
labels=plt_labels,plot_datapoints=False, title_quantiles=[0.16, 0.5, 0.84], label_kwargs={"fontsize":24}, 
title_kwargs={"fontsize":16}, max_n_ticks=4, bins=25, title_fmt='3.3g', plot_density=False, fill_contours=True,
levels=(0.393, 0.865, 0.989), hist_kwargs={'linewidth':0.75, 'color':cmap(0.75)},
contour_kwargs={'linewidths':0.5, 'colors':'black'}, 
contourf_kwargs={'colors':(cmap(-1), cmap(0.25), cmap(0.75), cmap(0.999)), 'alpha':0.75})

for axis in cornerFig.axes:
    axis.tick_params(axis='both', which='major', labelsize=16)

corner.overplot_lines(cornerFig, lmfit_params, color='C0', label='Least squares')
corner.overplot_points(cornerFig, np.array([lmfit_params]), color='C0', marker='s', ms=5)
corner.overplot_lines(cornerFig, median_values, color='black', label='Median')
corner.overplot_points(cornerFig, np.array([median_values]), color='black', marker='s', ms=5)

handles,labels = cornerFig.gca().get_legend_handles_labels()
by_label = dict(zip(labels, handles))
cornerFig.legend(by_label.values(), by_label.keys(), fontsize=24)
cornerFig.set_facecolor('white')
plt.savefig('../figures/V410Tau_corner.png', bbox_inches='tight')
plt.savefig('../figures/V410Tau_corner.pdf', bbox_inches='tight')
cornerFig.show()